Clone the repo from GitHub

In [1]:
!git clone https://github.com/NVIDIA/tacotron2.git
%cd tacotron2
!git submodule init; git submodule update

Cloning into 'tacotron2'...
remote: Enumerating objects: 412, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 412 (delta 2), reused 3 (delta 0), pack-reused 406
Receiving objects: 100% (412/412), 2.70 MiB | 23.45 MiB/s, done.
Resolving deltas: 100% (202/202), done.
/kaggle/working/tacotron2
Submodule 'waveglow' (https://github.com/NVIDIA/waveglow) registered for path 'waveglow'
Cloning into '/kaggle/working/tacotron2/waveglow'...
Submodule path 'waveglow': checked out '5bc2a53e20b3b533362f974cfa1ea0267ae1c2b1'


Create file lists from train and validation sets

In [2]:
import pandas as pd

metadata = pd.read_csv("../../input/happy/metadata.csv")

total = len(metadata)
split = 0.95
train = int(total * split)

train_metadata = metadata[:train]
val_metadata = metadata[train:]

with open('filelists/audio_text_train_filelist.txt', 'w') as f:
    for _, (index, text, _) in train_metadata.iterrows():
        filepath = '/kaggle/input/happy/wavs/%d.wav' % index
        f.write(filepath + '|' + text + '\n')

with open('filelists/audio_text_test_filelist.txt', 'w') as f:
    for _, (index, text, _) in val_metadata.iterrows():
        filepath = '/kaggle/input/happy/wavs/%d.wav' % index
        f.write(filepath + '|' + text + '\n')
        
print('yay')

yay


Install dependencies

In [3]:
!pip install tensorflow==1.15
!pip install unidecode
!pip install inflect

     |████████████████████████████████| 412.3 MB 19 kB/s s eta 0:00:01     |██████████▎                     | 131.8 MB 15.2 MB/s eta 0:00:19��████▋           | 265.8 MB 59.1 MB/s eta 0:00:03     |███████████████████████████     | 348.9 MB 11.5 MB/s eta 0:00:06     |███████████████████████████▎    | 351.5 MB 11.5 MB/s eta 0:00:06     |███████████████████████████▍    | 353.0 MB 11.5 MB/s eta 0:00:06     |███████████████████████████▌    | 354.4 MB 11.5 MB/s eta 0:00:06     |████████████████████████████    | 360.2 MB 11.5 MB/s eta 0:00:05     |████████████████████████████    | 361.5 MB 11.5 MB/s eta 0:00:05     |█████████████████████████████   | 372.4 MB 11.5 MB/s eta 0:00:04     |█████████████████████████████▍  | 378.3 MB 32.6 MB/s eta 0:00:02     |█████████████████████████████▌  | 379.9 MB 32.6 MB/s eta 0:00:01
     |████████████████████████████████| 50 kB 5.1 MB/s  eta 0:00:01
     |████████████████████████████████| 3.8 MB 45.8 MB/s eta 0:00:01
     |████████████████████████████████| 50

Download pretrained model from Google Drive for transfer learning

In [4]:
ls

Dockerfile           distributed.py   loss_function.py   stft.py
LICENSE              filelists/       loss_scaler.py     tensorboard.png
README.md*           hparams.py       model.py           text/
audio_processing.py  inference.ipynb  multiproc.py       train.py
data_utils.py        layers.py        plotting_utils.py  utils.py
demo.wav*            logger.py        requirements.txt   waveglow/


In [5]:
!pip install gdown
!gdown https://drive.google.com/uc?id=1c5ZTuT7J08wLUoVZ2KkUs_VdZuJ86ZqA

     |████████████████████████████████| 142 kB 8.9 MB/s eta 0:00:01
Downloading...
From (uriginal): https://drive.google.com/uc?id=1c5ZTuT7J08wLUoVZ2KkUs_VdZuJ86ZqA
From (redirected): https://drive.google.com/uc?id=1c5ZTuT7J08wLUoVZ2KkUs_VdZuJ86ZqA&confirm=t&uuid=299063ea-355a-46bb-901e-15e27112015d
To: /kaggle/working/tacotron2/tacotron2_statedict.pt
100%|█████████████████████████████████████████| 113M/113M [00:00<00:00, 146MB/s]


Train the model for 1000 epochs with a batch size of 32

In [6]:
pwd

'/kaggle/working/tacotron2'

In [7]:
# %load hparams.py
import tensorflow as tf
from text import symbols


def create_hparams(hparams_string=None, verbose=False):
    """Create model hyperparameters. Parse nondefault from given string."""

    hparams = tf.contrib.training.HParams(
        ################################
        # Experiment Parameters        #
        ################################
        epochs=500,
        iters_per_checkpoint=1000,
        seed=1234,
        dynamic_loss_scaling=True,
        fp16_run=False,
        distributed_run=False,
        dist_backend="nccl",
        dist_url="tcp://localhost:54321",
        cudnn_enabled=True,
        cudnn_benchmark=False,
        ignore_layers=['embedding.weight'],

        ################################
        # Data Parameters             #
        ################################
        load_mel_from_disk=False,
        training_files='filelists/ljs_audio_text_train_filelist.txt',
        validation_files='filelists/ljs_audio_text_val_filelist.txt',
        text_cleaners=['english_cleaners'],

        ################################
        # Audio Parameters             #
        ################################
        max_wav_value=32768.0,
        sampling_rate=22050,
        filter_length=1024,
        hop_length=256,
        win_length=1024,
        n_mel_channels=80,
        mel_fmin=0.0,
        mel_fmax=8000.0,

        ################################
        # Model Parameters             #
        ################################
        n_symbols=len(symbols),
        symbols_embedding_dim=512,

        # Encoder parameters
        encoder_kernel_size=5,
        encoder_n_convolutions=3,
        encoder_embedding_dim=512,

        # Decoder parameters
        n_frames_per_step=1,  # currently only 1 is supported
        decoder_rnn_dim=1024,
        prenet_dim=256,
        max_decoder_steps=1000,
        gate_threshold=0.5,
        p_attention_dropout=0.1,
        p_decoder_dropout=0.1,

        # Attention parameters
        attention_rnn_dim=1024,
        attention_dim=128,

        # Location Layer parameters
        attention_location_n_filters=32,
        attention_location_kernel_size=31,

        # Mel-post processing network parameters
        postnet_embedding_dim=512,
        postnet_kernel_size=5,
        postnet_n_convolutions=5,

        ################################
        # Optimization Hyperparameters #
        ################################
        use_saved_learning_rate=False,
        learning_rate=1e-3,
        weight_decay=1e-6,
        grad_clip_thresh=1.0,
        batch_size=64,
        mask_padding=True  # set model's padded outputs to padded values
    )

    if hparams_string:
        tf.logging.info('Parsing command line hparams: %s', hparams_string)
        hparams.parse(hparams_string)

    if verbose:
        tf.logging.info('Final parsed hparams: %s', hparams.values())

    return hparams


In [8]:
%%writefile hparams.py
import tensorflow as tf
from text import symbols


def create_hparams(hparams_string=None, verbose=False):
    """Create model hyperparameters. Parse nondefault from given string."""

    hparams = tf.contrib.training.HParams(
        ################################
        # Experiment Parameters        #
        ################################
        epochs=3,
        iters_per_checkpoint=10,
        seed=1234,
        dynamic_loss_scaling=True,
        fp16_run=False,
        distributed_run=False,
        dist_backend="nccl",
        dist_url="tcp://localhost:54321",
        cudnn_enabled=True,
        cudnn_benchmark=False,
        ignore_layers=['embedding.weight'],

        ################################
        # Data Parameters             #
        ################################
        load_mel_from_disk=False,
        training_files='/kaggle/working/tacotron2/filelists/audio_text_train_filelist.txt',
        validation_files='/kaggle/working/tacotron2/filelists/audio_text_test_filelist.txt',
        text_cleaners=['english_cleaners'],

        ################################
        # Audio Parameters             #
        ################################
        max_wav_value=32768.0,
        sampling_rate=22050,
        filter_length=1024,
        hop_length=256,
        win_length=1024,
        n_mel_channels=80,
        mel_fmin=0.0,
        mel_fmax=8000.0,

        ################################
        # Model Parameters             #
        ################################
        n_symbols=len(symbols),
        symbols_embedding_dim=512,

        # Encoder parameters
        encoder_kernel_size=5,
        encoder_n_convolutions=3,
        encoder_embedding_dim=512,

        # Decoder parameters
        n_frames_per_step=1,  # currently only 1 is supported
        decoder_rnn_dim=1024,
        prenet_dim=256,
        max_decoder_steps=1000,
        gate_threshold=0.5,
        p_attention_dropout=0.1,
        p_decoder_dropout=0.1,

        # Attention parameters
        attention_rnn_dim=1024,
        attention_dim=128,

        # Location Layer parameters
        attention_location_n_filters=32,
        attention_location_kernel_size=31,

        # Mel-post processing network parameters
        postnet_embedding_dim=512,
        postnet_kernel_size=5,
        postnet_n_convolutions=5,

        ################################
        # Optimization Hyperparameters #
        ################################
        use_saved_learning_rate=False,
        learning_rate=1e-4,
        weight_decay=1e-6,
        grad_clip_thresh=1.0,
        batch_size=32,
        mask_padding=True  # set model's padded outputs to padded values
    )

    if hparams_string:
        tf.logging.info('Parsing command line hparams: %s', hparams_string)
        hparams.parse(hparams_string)

    if verbose:
        tf.logging.info('Final parsed hparams: %s', hparams.values())

    return hparams

Overwriting hparams.py


In [9]:
# %load hparams.py
import tensorflow as tf
from text import symbols


def create_hparams(hparams_string=None, verbose=False):
    """Create model hyperparameters. Parse nondefault from given string."""

    hparams = tf.contrib.training.HParams(
        ################################
        # Experiment Parameters        #
        ################################
        epochs=3,
        iters_per_checkpoint=10,
        seed=1234,
        dynamic_loss_scaling=True,
        fp16_run=False,
        distributed_run=False,
        dist_backend="nccl",
        dist_url="tcp://localhost:54321",
        cudnn_enabled=True,
        cudnn_benchmark=False,
        ignore_layers=['embedding.weight'],

        ################################
        # Data Parameters             #
        ################################
        load_mel_from_disk=False,
        training_files='/kaggle/working/tacotron2/filelists/audio_text_train_filelist.txt',
        validation_files='/kaggle/working/tacotron2/filelists/audio_text_test_filelist.txt',
        text_cleaners=['english_cleaners'],

        ################################
        # Audio Parameters             #
        ################################
        max_wav_value=32768.0,
        sampling_rate=22050,
        filter_length=1024,
        hop_length=256,
        win_length=1024,
        n_mel_channels=80,
        mel_fmin=0.0,
        mel_fmax=8000.0,

        ################################
        # Model Parameters             #
        ################################
        n_symbols=len(symbols),
        symbols_embedding_dim=512,

        # Encoder parameters
        encoder_kernel_size=5,
        encoder_n_convolutions=3,
        encoder_embedding_dim=512,

        # Decoder parameters
        n_frames_per_step=1,  # currently only 1 is supported
        decoder_rnn_dim=1024,
        prenet_dim=256,
        max_decoder_steps=1000,
        gate_threshold=0.5,
        p_attention_dropout=0.1,
        p_decoder_dropout=0.1,

        # Attention parameters
        attention_rnn_dim=1024,
        attention_dim=128,

        # Location Layer parameters
        attention_location_n_filters=32,
        attention_location_kernel_size=31,

        # Mel-post processing network parameters
        postnet_embedding_dim=512,
        postnet_kernel_size=5,
        postnet_n_convolutions=5,

        ################################
        # Optimization Hyperparameters #
        ################################
        use_saved_learning_rate=False,
        learning_rate=1e-4,
        weight_decay=1e-6,
        grad_clip_thresh=1.0,
        batch_size=32,
        mask_padding=True  # set model's padded outputs to padded values
    )

    if hparams_string:
        tf.logging.info('Parsing command line hparams: %s', hparams_string)
        hparams.parse(hparams_string)

    if verbose:
        tf.logging.info('Final parsed hparams: %s', hparams.values())

    return hparams


In [10]:
!python train.py --output_directory=outdir --log_directory=logdir -c tacotron2_statedict.pt --warm_start --hparams sampling_rate=22050

FP16 Run: False
Dynamic Loss Scaling: True
Distributed Run: False
cuDNN Enabled: True
cuDNN Benchmark: False
Warm starting model from checkpoint 'tacotron2_statedict.pt'
Epoch: 0
Train loss 0 0.702485 Grad Norm 5.941093 4.36s/it
Validation loss 0:  0.776477  
Saving model and optimizer state at iteration 0 to outdir/checkpoint_0
Train loss 1 0.633042 Grad Norm 27.295851 3.32s/it
Train loss 2 0.531299 Grad Norm 3.390558 4.57s/it
Train loss 3 0.599854 Grad Norm 47.498989 3.61s/it
Train loss 4 0.511869 Grad Norm 1.984578 5.03s/it
Train loss 5 0.515077 Grad Norm 812.600281 4.55s/it
Train loss 6 0.477849 Grad Norm 2.079429 4.09s/it
Train loss 7 0.552566 Grad Norm 1.768882 2.74s/it
Epoch: 1
Train loss 8 0.453636 Grad Norm 1.004837 4.71s/it
Train loss 9 0.444428 Grad Norm 1.297991 3.18s/it
Train loss 10 0.418960 Grad Norm 1.133567 4.07s/it
Validation loss 10:  0.446415  
Saving model and optimizer state at iteration 10 to outdir/checkpoint_10
Train loss 11 0.408512 Grad Norm 0.851174 3.99s/it

## Inference
### Synthesize generated audio samples from text

In [11]:
ls

Dockerfile           hparams.py        plotting_utils.py
LICENSE              inference.ipynb   requirements.txt
README.md*           layers.py         stft.py
__pycache__/         logger.py         tacotron2_statedict.pt
audio_processing.py  loss_function.py  tensorboard.png
data_utils.py        loss_scaler.py    text/
demo.wav*            model.py          train.py
distributed.py       multiproc.py      utils.py
filelists/           outdir/           waveglow/


In [12]:
!python -m pip install spacy

In [13]:
!pip install inflect==5.0.1

  Attempting uninstall: inflect
    Found existing installation: inflect 6.0.5
    Uninstalling inflect-6.0.5:
      Successfully uninstalled inflect-6.0.5


In [14]:
from multiprocessing import Pool
import matplotlib.pylab as plt
%matplotlib inline
from tqdm.notebook import tqdm
import IPython.display as ipd
from time import time, sleep
import scipy.io.wavfile
import numpy as np
import matplotlib
import torch
import sys

sys.path.append('waveglow/')

from audio_processing import griffin_lim
from layers import TacotronSTFT, STFT
from hparams import create_hparams
from text import text_to_sequence
from denoiser import Denoiser
from train import load_model
from model import Tacotron2

In [15]:
def plot_data(data, figsize=(16, 4)):
    fig, axes = plt.subplots(1, len(data), figsize=figsize)
    for i in range(len(data)):
        axes[i].imshow(data[i], aspect='auto', origin='lower', interpolation='none')

In [16]:
hparams = create_hparams()
hparams.sampling_rate = 22050

In [17]:
checkpoint = int(input("Enter steps at latest checkpoint: "))
checkpoint_path = f"outdir/checkpoint_0"
model = load_model(hparams)
model.load_state_dict(torch.load(checkpoint_path)['state_dict'])
_ = model.cuda().eval().half()

Enter steps at latest checkpoint:  10


In [18]:
!gdown https://drive.google.com/uc?id=1rpK8CzAAirq9sWZhe9nlfvxMF1dRgFbF

Downloading...
From (uriginal): https://drive.google.com/uc?id=1rpK8CzAAirq9sWZhe9nlfvxMF1dRgFbF
From (redirected): https://drive.google.com/uc?id=1rpK8CzAAirq9sWZhe9nlfvxMF1dRgFbF&confirm=t&uuid=286f5146-f695-49e0-a22a-accc5d7d557a
To: /kaggle/working/tacotron2/waveglow_256channels_universal_v5.pt
100%|█████████████████████████████████████████| 676M/676M [00:05<00:00, 121MB/s]


In [19]:
waveglow_path = 'waveglow_256channels_universal_v5.pt'
waveglow = torch.load(waveglow_path)['model']
waveglow.cuda().eval().half()
for k in waveglow.convinv:
    k.float()
denoiser = Denoiser(waveglow)

/opt/conda/lib/python3.7/site-packages/torch/serialization.py:658: SourceChangeWarning: source code of class 'torch.nn.modules.conv.ConvTranspose1d' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/opt/conda/lib/python3.7/site-packages/torch/serialization.py:658: SourceChangeWarning: source code of class 'torch.nn.modules.container.ModuleList' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/opt/conda/lib/python3.7/site-packages/torch/serialization.py:658: SourceChangeWarning: source code of class 'torch.nn.modules.conv.Conv1d' has changed. you can retrieve the original source code by accessing the object's source attribute or

In [20]:
def synthesize(word, n=5, cleaners=['english_cleaners'], sigma=0.666, strength=0.01):
    sequence = np.array(text_to_sequence(word, cleaners))[None, :]
    sequence = torch.autograd.Variable(torch.from_numpy(sequence)).cuda().long()
    with torch.no_grad():
        mel_outputs, mel_outputs_postnet, _, alignments = model.inference(sequence)
    audio = waveglow.infer(mel_outputs_postnet, sigma=sigma)
    audio_denoised = denoiser(audio, strength=strength)[:, 0]
    audio = audio[0].data.cpu().numpy().tolist()
    mel_outputs = mel_outputs.float().data.cpu().numpy()[0]
    mel_outputs_postnet = mel_outputs_postnet.float().data.cpu().numpy()[0]
    alignments = alignments.float().data.cpu().numpy()[0]
    return audio, mel_outputs, mel_outputs_postnet, alignments

In [21]:
tests = [
         "Scientists at the CERN laboratory say they have discovered a new particle.",
         "The state of Florida reports a surge in coronavirus deaths as restrictions are upended.",
         "How much wood would a woodchuck chuck if a woodchuck could chuck wood?",
         "A woodchuck would chuck all the wood it could chuck if a woodchuck could chuck wood.",
         "Peter Piper picked a peck of pickled peppers. How many pickled peppers did Peter Piper pick?",
         "Sally sells seashells by the seashore. The shells she sells are seashells I'm sure.",
         "The blue lagoon is a nineteen eighty American romance adventure film.",
         "George Washington was the first President of the United States.",
         "Basilar membrane and otolaryngology are not auto-correlations.",
         "Biden holds first foreign meeting with Canada's Justin Trudeau."
]

In [22]:
for text in tests:
    audio, mel_outputs, mel_outputs_postnet, alignments = synthesize(text, n=15)
    ipd.display_html(ipd.HTML(f"""
    <h3>{text}</h3>
    <br/>
    """))
    ipd.display(ipd.Audio(data = audio, rate = 22050, autoplay = False))

Warning! Reached max decoder steps


Scientists at the CERN laboratory say they have discovered a new particle.

Warning! Reached max decoder steps


The state of Florida reports a surge in coronavirus deaths as restrictions are upended.

Warning! Reached max decoder steps


...

George Washington was the first President of the United States.

Warning! Reached max decoder steps


Basilar membrane and otolaryngology are not auto-correlations.

Warning! Reached max decoder steps


Biden holds first foreign meeting with Canada's Justin Trudeau.